In [1]:
import configparser
import sys
import os
from snowflake.snowpark import Session
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from snowflake.snowpark.functions import col, sproc,udf
from snowflake.snowpark.types import StringType, Variant, ArrayType
import seaborn as sns
import snowflake

In [33]:

def makeSnowflakeConnection(connection_name):
    global config
    config = configparser.RawConfigParser()
    config.read('configConnection.properties')
    warehouse = config.get(connection_name, 'warehouse')
    user = config.get(connection_name, 'user')
    password =config.get(connection_name, 'password')
    account=config.get(connection_name, 'account')
    role=config.get(connection_name, 'role')
    conn = dict(
                user=user,
                password=password,
                account=account,
                warehouse=warehouse,
                role=role
                )
    session = Session.builder.configs(conn).create()
    return session


session=makeSnowflakeConnection('DBMS_PROJECT')

In [3]:
create_db_sql = """
CREATE OR REPLACE DATABASE COVID19_NEW;
"""
session.sql(create_db_sql).collect()

[Row(status='Database COVID19_NEW successfully created.')]

In [4]:
create_schema_sql = """
CREATE OR REPLACE SCHEMA RAW_DATA;
"""
session.sql(create_schema_sql).collect()

[Row(status='Schema RAW_DATA successfully created.')]

In [5]:
session.use_database('COVID19_NEW')
session.use_schema('RAW_DATA')

In [17]:
create_stage_sql = """
CREATE OR REPLACE STAGE TWITTER_DATA;
"""
session.sql(create_stage_sql).collect()

[Row(status='Stage area TWITTER_DATA successfully created.')]

In [7]:
create_query="""CREATE OR REPLACE TABLE original_tweets (
    created_at VARCHAR,
    id VARCHAR,
    text VARCHAR,
    source VARCHAR,
    truncated BOOLEAN,
    in_reply_to_status_id VARCHAR,
    in_reply_to_user_id VARCHAR,
    in_reply_to_screen_name VARCHAR,
    user_id VARCHAR,
    user_name VARCHAR,
    user_screen_name VARCHAR,
    user_location VARCHAR,
    user_description VARCHAR,
    user_protected BOOLEAN,
    user_followers_count NUMBER,
    user_friends_count NUMBER,
    user_listed_count NUMBER,
    user_favourites_count NUMBER,
    user_statuses_count NUMBER,
    user_created_at VARCHAR,
    user_utc_offset VARCHAR,
    user_time_zone VARCHAR,
    user_geo_enabled BOOLEAN,
    user_lang VARCHAR,
    geo VARCHAR,
    coordinates VARCHAR,
    place VARCHAR,
    contributors VARCHAR,
    is_quote_status BOOLEAN,
    quote_count NUMBER,
    reply_count NUMBER,
    retweet_count NUMBER,
    favorite_count NUMBER,
    entities_hashtags VARIANT,  -- Assuming this can be a nested structure
    entities_symbols VARIANT,   -- Assuming this can be a nested structure
    entities_user_mentions VARIANT,  -- Assuming this can be a nested structure
    entities_urls VARIANT,  -- Assuming this can be a nested structure
    lang VARCHAR,
    extended_tweet_full_text STRING,
    extended_entities_media VARIANT  -- If this contains nested JSON
);

"""
session.sql(create_query).collect()

[Row(status='Table ORIGINAL_TWEETS successfully created.')]

In [8]:
create_query="""
CREATE OR REPLACE TABLE retweets (
    created_at STRING,
    id STRING,
    text STRING,
    source STRING,
    truncated BOOLEAN,
    in_reply_to_status_id STRING,
    in_reply_to_user_id STRING,
    in_reply_to_screen_name STRING,
    user_id STRING,
    user_name STRING,
    user_screen_name STRING,
    user_location STRING,
    user_description STRING,
    user_protected BOOLEAN,
    user_followers_count NUMBER,
    user_friends_count NUMBER,
    user_listed_count NUMBER,
    user_favourites_count NUMBER,
    user_statuses_count NUMBER,
    user_created_at STRING,
    user_utc_offset STRING,
    user_time_zone STRING,
    user_geo_enabled BOOLEAN,
    user_lang STRING,
    geo STRING,
    coordinates STRING,
    place STRING,
    contributors STRING,
    is_quote_status BOOLEAN,
    quote_count NUMBER,
    reply_count NUMBER,
    retweet_count NUMBER,
    favorite_count NUMBER,
    entities_hashtags STRING,
    entities_symbols STRING,
    entities_user_mentions STRING,
    entities_urls STRING,
    lang STRING,
    original_tweet_id STRING,
    original_tweet_created_at STRING,
    original_tweet_text STRING,
    original_tweet_source STRING,
    original_tweet_truncated BOOLEAN,
    original_tweet_in_reply_to_status_id STRING,
    original_tweet_in_reply_to_user_id STRING,
    original_tweet_in_reply_to_screen_name STRING,
    original_tweet_user_id STRING,
    original_tweet_user_name STRING,
    original_tweet_user_screen_name STRING,
    original_tweet_user_location STRING,
    original_tweet_user_description STRING,
    original_tweet_user_protected BOOLEAN,
    original_tweet_user_followers_count NUMBER,
    original_tweet_user_friends_count NUMBER,
    original_tweet_user_listed_count NUMBER,
    original_tweet_user_favourites_count NUMBER,
    original_tweet_user_statuses_count NUMBER,
    original_tweet_user_created_at STRING,
    original_tweet_user_utc_offset STRING,
    original_tweet_user_time_zone STRING,
    original_tweet_user_geo_enabled BOOLEAN,
    original_tweet_user_lang STRING,
    original_tweet_geo STRING,
    original_tweet_coordinates STRING,
    original_tweet_place STRING,
    original_tweet_contributors STRING,
    original_tweet_is_quote_status BOOLEAN,
    original_tweet_quote_count NUMBER,
    original_tweet_reply_count NUMBER,
    original_tweet_retweet_count NUMBER,
    original_tweet_favorite_count NUMBER,
    original_tweet_entities_hashtags STRING,
    original_tweet_entities_symbols STRING,
    original_tweet_entities_user_mentions STRING,
    original_tweet_entities_urls STRING,
    original_tweet_lang STRING,
    original_tweet_extended_tweet_full_text STRING,
    original_tweet_extended_entities_media STRING
);
"""
session.sql(create_query).collect()

[Row(status='Table RETWEETS successfully created.')]

In [9]:
create_query="""
CREATE OR REPLACE TABLE combined_tweets (
    created_at STRING,
    id STRING,
    text STRING,
    source STRING,
    truncated BOOLEAN,
    in_reply_to_status_id STRING,
    in_reply_to_user_id STRING,
    in_reply_to_screen_name STRING,
    user_id STRING,
    user_name STRING,
    user_screen_name STRING,
    user_location STRING,
    user_description STRING,
    user_protected BOOLEAN,
    user_followers_count NUMBER,
    user_friends_count NUMBER,
    user_listed_count NUMBER,
    user_favourites_count NUMBER,
    user_statuses_count NUMBER,
    user_created_at STRING,
    user_utc_offset STRING,
    user_time_zone STRING,
    user_geo_enabled BOOLEAN,
    user_lang STRING,
    geo STRING,
    coordinates STRING,
    place STRING,
    contributors STRING,
    is_quote_status BOOLEAN,
    quote_count NUMBER,
    reply_count NUMBER,
    retweet_count NUMBER,
    favorite_count NUMBER,
    entities_hashtags STRING,
    entities_symbols STRING,
    entities_user_mentions STRING,
    entities_urls STRING,
    lang STRING,
    extended_tweet_full_text STRING,
    extended_entities_media STRING,
    tweet_type STRING  -- This column will indicate 'T' for tweet or 'RT' for retweet
);
"""
session.sql(create_query).collect()

[Row(status='Table COMBINED_TWEETS successfully created.')]

In [20]:
import os

folder_path = 'C:\\Users\\srinivas\\Desktop\\DBMS_Project\\corona\\*'
#files = [f for f in os.listdir(folder_path) if f.endswith('.json')]

In [22]:
# for file in files:
#full_path = os.path.join(folder_path, file)
put_command = f"PUT file:///{folder_path} @twitter_data AUTO_COMPRESS=TRUE PARALLEL = 99;"
session.sql(put_command).collect()

[Row(source='RT_1249403767180668930_20200412182725.json', target='RT_1249403767180668930_20200412182725.json.gz', source_size=13243, target_size=2384, source_compression='NONE', target_compression='GZIP', status='UPLOADED', message=''),
 Row(source='RT_1249403768023678982_20200412182725.json', target='RT_1249403768023678982_20200412182725.json.gz', source_size=7877, target_size=1888, source_compression='NONE', target_compression='GZIP', status='UPLOADED', message=''),
 Row(source='RT_1249403769193779202_20200412182726.json', target='RT_1249403769193779202_20200412182726.json.gz', source_size=43384, target_size=4272, source_compression='NONE', target_compression='GZIP', status='UPLOADED', message=''),
 Row(source='RT_1249403769567227906_20200412182726.json', target='RT_1249403769567227906_20200412182726.json.gz', source_size=7919, target_size=1952, source_compression='NONE', target_compression='GZIP', status='UPLOADED', message=''),
 Row(source='RT_1249403770435493888_20200412182726.jso

In [12]:
# all_files = os.listdir(folder_path)
# files = [f for f in all_files if f.startswith('T') and f.endswith('.json')]

# # Process only the first 10,000 files
# files = files[:20000]

In [14]:
# for file in files:
#     full_path = os.path.join(folder_path, file)
#     put_command = f"PUT file:///{full_path} @twitter_data AUTO_COMPRESS=TRUE PARALLEL = 99;"
#     session.sql(put_command).collect()


In [23]:
q="""
CREATE OR REPLACE TABLE staging_tweets (
    raw_data VARIANT
);
"""
session.sql(q).collect()


[Row(status='Table STAGING_TWEETS successfully created.')]

In [24]:
q="""
CREATE OR REPLACE TABLE staging_retweets (
    raw_data VARIANT
);
"""
session.sql(q).collect()


[Row(status='Table STAGING_RETWEETS successfully created.')]

In [25]:
q2="""
COPY INTO staging_tweets
FROM @twitter_data
FILE_FORMAT = (TYPE = 'JSON', COMPRESSION = 'GZIP')
PATTERN = 'T_.*\\.json\\.gz'
ON_ERROR = 'CONTINUE';
"""
session.sql(q2).collect()


[Row(file='twitter_data/T_1249403773799170049_20200412182727.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(file='twitter_data/T_1249403777544859650_20200412182728.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(file='twitter_data/T_1249403784197013505_20200412182729.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(file='twitter_data/T_1249403785375617028_20200412182729.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(fil

In [26]:
q2="""
COPY INTO staging_retweets
FROM @twitter_data
FILE_FORMAT = (TYPE = 'JSON', COMPRESSION = 'GZIP')
PATTERN = 'RT_.*\\.json\\.gz'
ON_ERROR = 'ABORT_STATEMENT';
"""
session.sql(q2).collect()


[Row(file='twitter_data/RT_1249403771077005315_20200412182726.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(file='twitter_data/RT_1249403773476356096_20200412182727.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(file='twitter_data/RT_1249403776441737216_20200412182727.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row(file='twitter_data/RT_1249403779906035718_20200412182728.json.gz', status='LOADED', rows_parsed=1, rows_loaded=1, error_limit=1, errors_seen=0, first_error=None, first_error_line=None, first_error_character=None, first_error_column_name=None),
 Row

In [27]:
query="""
INSERT INTO original_tweets (
    created_at,
    id,
    text,
    source,
    truncated,
    in_reply_to_status_id,
    in_reply_to_user_id,
    in_reply_to_screen_name,
    user_id,
    user_name,
    user_screen_name,
    user_location,
    user_description,
    user_protected,
    user_followers_count,
    user_friends_count,
    user_listed_count,
    user_favourites_count,
    user_statuses_count,
    user_created_at,
    user_utc_offset,
    user_time_zone,
    user_geo_enabled,
    user_lang,
    geo,
    coordinates,
    place,
    contributors,
    is_quote_status,
    quote_count,
    reply_count,
    retweet_count,
    favorite_count,
    entities_hashtags,
    entities_symbols,
    entities_user_mentions,
    entities_urls,
    lang,
    extended_tweet_full_text,
    extended_entities_media
)
SELECT
    raw_data:created_at::STRING,
    raw_data:id::STRING,
    raw_data:text::STRING,
    raw_data:source::STRING,
    raw_data:truncated::BOOLEAN,
    raw_data:in_reply_to_status_id::STRING,
    raw_data:in_reply_to_user_id::STRING,
    raw_data:in_reply_to_screen_name::STRING,
    raw_data:user:id::STRING,
    raw_data:user:name::STRING,
    raw_data:user:screen_name::STRING,
    raw_data:user:location::STRING,
    raw_data:user:description::STRING,
    raw_data:user:protected::BOOLEAN,
    raw_data:user:followers_count::NUMBER,
    raw_data:user:friends_count::NUMBER,
    raw_data:user:listed_count::NUMBER,
    raw_data:user:favourites_count::NUMBER,
    raw_data:user:statuses_count::NUMBER,
    raw_data:user:created_at::STRING,
    raw_data:user:utc_offset::STRING,
    raw_data:user:time_zone::STRING,
    raw_data:user:geo_enabled::BOOLEAN,
    raw_data:user:lang::STRING,
    raw_data:geo::STRING,
    raw_data:coordinates::STRING,
    raw_data:place::STRING,
    raw_data:contributors::STRING,
    raw_data:is_quote_status::BOOLEAN,
    raw_data:quote_count::NUMBER,
    raw_data:reply_count::NUMBER,
    raw_data:retweet_count::NUMBER,
    raw_data:favorite_count::NUMBER,
    raw_data:entities:hashtags::VARIANT,
    raw_data:entities:symbols::VARIANT,
    raw_data:entities:user_mentions::VARIANT,
    raw_data:entities:urls::VARIANT,
    raw_data:lang::STRING,
    raw_data:extended_tweet:full_text::STRING,
    raw_data:extended_entities:media::VARIANT
FROM staging_tweets;
"""
session.sql(query).collect()


[Row(number of rows inserted=48142)]

In [28]:
query="""
INSERT INTO retweets (
    created_at,
    id,
    text,
    source,
    truncated,
    in_reply_to_status_id,
    in_reply_to_user_id,
    in_reply_to_screen_name,
    user_id,
    user_name,
    user_screen_name,
    user_location,
    user_description,
    user_protected,
    user_followers_count,
    user_friends_count,
    user_listed_count,
    user_favourites_count,
    user_statuses_count,
    user_created_at,
    user_utc_offset,
    user_time_zone,
    user_geo_enabled,
    user_lang,
    geo,
    coordinates,
    place,
    contributors,
    is_quote_status,
    quote_count,
    reply_count,
    retweet_count,
    favorite_count,
    entities_hashtags,
    entities_symbols,
    entities_user_mentions,
    entities_urls,
    lang,
    original_tweet_id,
    original_tweet_created_at,
    original_tweet_text,
    original_tweet_source,
    original_tweet_truncated,
    original_tweet_in_reply_to_status_id,
    original_tweet_in_reply_to_user_id,
    original_tweet_in_reply_to_screen_name,
    original_tweet_user_id,
    original_tweet_user_name,
    original_tweet_user_screen_name,
    original_tweet_user_location,
    original_tweet_user_description,
    original_tweet_user_protected,
    original_tweet_user_followers_count,
    original_tweet_user_friends_count,
    original_tweet_user_listed_count,
    original_tweet_user_favourites_count,
    original_tweet_user_statuses_count,
    original_tweet_user_created_at,
    original_tweet_user_utc_offset,
    original_tweet_user_time_zone,
    original_tweet_user_geo_enabled,
    original_tweet_user_lang,
    original_tweet_geo,
    original_tweet_coordinates,
    original_tweet_place,
    original_tweet_contributors,
    original_tweet_is_quote_status,
    original_tweet_quote_count,
    original_tweet_reply_count,
    original_tweet_retweet_count,
    original_tweet_favorite_count,
    original_tweet_entities_hashtags,
    original_tweet_entities_symbols,
    original_tweet_entities_user_mentions,
    original_tweet_entities_urls,
    original_tweet_lang,
    original_tweet_extended_tweet_full_text,
    original_tweet_extended_entities_media
)
SELECT
    raw_data:created_at::STRING,
    raw_data:id::STRING,
    raw_data:text::STRING,
    raw_data:source::STRING,
    raw_data:truncated::BOOLEAN,
    raw_data:in_reply_to_status_id::STRING,
    raw_data:in_reply_to_user_id::STRING,
    raw_data:in_reply_to_screen_name::STRING,
    raw_data:user:id::STRING,
    raw_data:user:name::STRING,
    raw_data:user:screen_name::STRING,
    raw_data:user:location::STRING,
    raw_data:user:description::STRING,
    raw_data:user:protected::BOOLEAN,
    raw_data:user:followers_count::NUMBER,
    raw_data:user:friends_count::NUMBER,
    raw_data:user:listed_count::NUMBER,
    raw_data:user:favourites_count::NUMBER,
    raw_data:user:statuses_count::NUMBER,
    raw_data:user:created_at::STRING,
    raw_data:user:utc_offset::STRING,
    raw_data:user:time_zone::STRING,
    raw_data:user:geo_enabled::BOOLEAN,
    raw_data:user:lang::STRING,
    raw_data:geo::STRING,
    raw_data:coordinates::STRING,
    raw_data:place::STRING,
    raw_data:contributors::STRING,
    raw_data:is_quote_status::BOOLEAN,
    raw_data:quote_count::NUMBER,
    raw_data:reply_count::NUMBER,
    raw_data:retweet_count::NUMBER,
    raw_data:favorite_count::NUMBER,
    raw_data:entities:hashtags::VARIANT AS entities_hashtags,
    raw_data:entities:symbols::VARIANT AS entities_symbols,
    raw_data:entities:user_mentions::VARIANT AS entities_user_mentions,
    raw_data:entities:urls::VARIANT AS entities_urls,
    raw_data:lang::STRING,
    raw_data:retweeted_status:id::STRING AS original_tweet_id,
    raw_data:retweeted_status:created_at::STRING AS original_tweet_created_at,
    raw_data:retweeted_status:text::STRING AS original_tweet_text,
    raw_data:retweeted_status:source::STRING AS original_tweet_source,
    raw_data:retweeted_status:truncated::BOOLEAN AS original_tweet_truncated,
    raw_data:retweeted_status:in_reply_to_status_id::STRING AS original_tweet_in_reply_to_status_id,
    raw_data:retweeted_status:in_reply_to_user_id::STRING AS original_tweet_in_reply_to_user_id,
    raw_data:retweeted_status:in_reply_to_screen_name::STRING AS original_tweet_in_reply_to_screen_name,
    raw_data:retweeted_status:user:id::STRING AS original_tweet_user_id,
    raw_data:retweeted_status:user:name::STRING AS original_tweet_user_name,
    raw_data:retweeted_status:user:screen_name::STRING AS original_tweet_user_screen_name,
    raw_data:retweeted_status:user:location::STRING AS original_tweet_user_location,
    raw_data:retweeted_status:user:description::STRING AS original_tweet_user_description,
    raw_data:retweeted_status:user:protected::BOOLEAN AS original_tweet_user_protected,
    raw_data:retweeted_status:user:followers_count::NUMBER AS original_tweet_user_followers_count,
    raw_data:retweeted_status:user:friends_count::NUMBER AS original_tweet_user_friends_count,
    raw_data:retweeted_status:user:listed_count::NUMBER AS original_tweet_user_listed_count,
    raw_data:retweeted_status:user:favourites_count::NUMBER AS original_tweet_user_favourites_count,
    raw_data:retweeted_status:user:statuses_count::NUMBER AS original_tweet_user_statuses_count,
    raw_data:retweeted_status:user:created_at::STRING AS original_tweet_user_created_at,
    raw_data:retweeted_status:user:utc_offset::STRING AS original_tweet_user_utc_offset,
    raw_data:retweeted_status:user:time_zone::STRING AS original_tweet_user_time_zone,
    raw_data:retweeted_status:user:geo_enabled::BOOLEAN AS original_tweet_user_geo_enabled,
    raw_data:retweeted_status:user:lang::STRING AS original_tweet_user_lang,
    raw_data:retweeted_status:geo::STRING AS original_tweet_geo,
    raw_data:retweeted_status:coordinates::STRING AS original_tweet_coordinates,
    raw_data:retweeted_status:place::STRING AS original_tweet_place,
    raw_data:retweeted_status:contributors::STRING AS original_tweet_contributors,
    raw_data:retweeted_status:is_quote_status::BOOLEAN AS original_tweet_is_quote_status,
    raw_data:retweeted_status:quote_count::NUMBER AS original_tweet_quote_count,
    raw_data:retweeted_status:reply_count::NUMBER AS original_tweet_reply_count,
    raw_data:retweeted_status:retweet_count::NUMBER AS original_tweet_retweet_count,
    raw_data:retweeted_status:favorite_count::NUMBER AS original_tweet_favorite_count,
    raw_data:retweeted_status:entities:hashtags::VARIANT AS original_tweet_entities_hashtags,
    raw_data:retweeted_status:entities:symbols::VARIANT AS original_tweet_entities_symbols,
    raw_data:retweeted_status:entities:user_mentions::VARIANT AS original_tweet_entities_user_mentions,
    raw_data:retweeted_status:entities:urls::VARIANT AS original_tweet_entities_urls,
    raw_data:retweeted_status:lang::STRING AS original_tweet_lang,
    raw_data:retweeted_status:extended_tweet:full_text::STRING AS original_tweet_extended_tweet_full_text,
    raw_data:retweeted_status:extended_entities:media::VARIANT AS original_tweet_extended_entities_media
FROM staging_retweets;
"""
session.sql(query).collect()



[Row(number of rows inserted=72258)]

In [29]:
import os
import json
import pandas as pd
import numpy as np

# Assuming 'session' is an established Snowpark session

# Define the columns of the dataframe based on the user attributes
columns = [
    'id', 'id_str', 'name', 'screen_name', 'location', 'url', 'description',
    'translator_type', 'protected', 'verified', 'followers_count', 'friends_count',
    'listed_count', 'favourites_count', 'statuses_count', 'created_at',
    'utc_offset', 'time_zone', 'geo_enabled', 'lang', 'contributors_enabled',
    'is_translator', 'profile_background_color', 'profile_background_image_url',
    'profile_background_image_url_https', 'profile_background_tile', 'profile_link_color',
    'profile_sidebar_border_color', 'profile_sidebar_fill_color', 'profile_text_color',
    'profile_use_background_image', 'profile_image_url', 'profile_image_url_https',
    'profile_banner_url', 'default_profile', 'default_profile_image', 'following',
    'follow_request_sent', 'notifications'
]

# Initialize the dataframe for user data
user_df = pd.DataFrame(columns=columns)
seen_users = set()

# List files in the Snowflake stage
stage_name = 'TWITTER_DATA'  # Replace with your actual stage name
stage_files_query = session.sql(f"LIST @{stage_name}").collect()
stage_files = [file['name'] for file in stage_files_query]  # Assuming 'name' is the correct key

# Path to the local directory containing JSON files
local_directory = 'corona/'

for file in stage_files:
    # Assuming the file name in the stage is the same as the local file name minus '.gz'
    json_file_name = file.replace('.gz', '').replace('twitter_data/', '')
    print(json_file_name)
    # Path to the local JSON file
    local_file_path = os.path.join(local_directory, json_file_name)

    # Check if the local file exists and then process it
    if os.path.exists(local_file_path):
        with open(local_file_path, 'r', encoding='utf-8') as f:
            try:
                data = json.load(f)
                user_data = data.get('user', {})
                user_id = user_data.get('id_str', '')

                if user_id and user_id not in seen_users:
                    seen_users.add(user_id)
                    new_row_data = {col: user_data.get(col, np.nan) for col in columns}
                    new_row = pd.DataFrame([new_row_data])
                    user_df = pd.concat([user_df, new_row], ignore_index=True)

            except json.JSONDecodeError as e:
                print(f"Error decoding JSON from file {local_file_path}: {e}")

# Display or process the user dataframe as needed
print(user_df.head())


RT_1249403767180668930_20200412182725.json
RT_1249403768023678982_20200412182725.json
RT_1249403769193779202_20200412182726.json
RT_1249403769567227906_20200412182726.json
RT_1249403770435493888_20200412182726.json
RT_1249403770833981440_20200412182726.json
RT_1249403771077005315_20200412182726.json
RT_1249403771676815361_20200412182726.json
RT_1249403773178560515_20200412182726.json
RT_1249403773476356096_20200412182727.json
RT_1249403773522337792_20200412182727.json
RT_1249403773740552193_20200412182727.json
RT_1249403774151659521_20200412182727.json
RT_1249403775229534209_20200412182727.json
RT_1249403775493816321_20200412182727.json
RT_1249403775632076801_20200412182727.json
RT_1249403776441737216_20200412182727.json
RT_1249403777498542081_20200412182728.json
RT_1249403777804840962_20200412182728.json
RT_1249403778241044483_20200412182728.json
RT_1249403778895314956_20200412182728.json
RT_1249403779440463872_20200412182728.json
RT_1249403779692335106_20200412182728.json
RT_12494037

In [32]:
user_df

id               id_str                name  \
0      1242817830946508801  1242817830946508801            juwelz v   
1      1225145123920588805  1225145123920588805               efe09   
2                101007632            101007632         Ravin Gupta   
3      1230170166614482944  1230170166614482944          Carpe diem   
4               4707764075           4707764075  UpsidedownTurtle 🧢   
...                    ...                  ...                 ...   
95649   892116055048548354   892116055048548354         'Mr. Right'   
95650  1201144872754909187  1201144872754909187            luan ⚔️💓   
95651   734263483173212160   734263483173212160          dirty d 😽💙   
95652  1250325547848089600  1250325547848089600          Kumar Amit   
95653           2279976427           2279976427            Venugopi   

           screen_name                    location  \
0             juwelz_v  Lower East Side, Manhattan   
1        efe0927183508                        None   
2            IamRaavin                       india   
3      Carpedi92670638                        None   
4              Adakisn                        None   
...                ...                         ...   
95649  realtrumpster01                        None   
95650        swtunluan              Ꮻ 𝐂𝐇𝐑𝐎𝐌𝐀𝐓𝐈𝐂𝐀 Ꮻ   
95651      deannarae21                 baerobbie 💙   
95652  Amitkum94252986                        None   
95653         Venu7630                        None   

                                    url  \
0             https://linktr.ee/juwelzv   
1                                  None   
2                                  None   
3                                  None   
4                                  None   
...                                 ...   
95649  http://buymeacoff.ee/noleftturns   
95650       http://reputation.xn--4n8h/   
95651                              None   
95652                              None   
95653                              None   

                                             description translator_type  \
0      Event Lyfe LLC .. Brand Ambassador: #visionary...            none   
1      Allah'ın en değerli eseri insandır.\nCanı yana...            none   
2      Tweet is personal opinion and Retweet is not e...            none   
3                Yezidin hârcı zulüm\nYiğidin burcu ölüm            none   
4                                                   None            none   
...                                                  ...             ...   
95649  While President Trump Makes America Great Agai...            none   
95650  「𝙛𝙖𝙣 𝙖𝙘𝙘𝙤𝙪𝙣𝙩」\n\n𝖆𝖗𝖎𝖆𝖓𝖆𝖙𝖔𝖗 | #CHROMATICA\n\n𝖗𝖊...            none   
95651        the snack that smiles back ♏️ chico state 💫            none   
95652    सेकुलर के नाम पर भारत में। सनातन धर्म खतरे में।            none   
95653                                               None            none   

      protected verified  ... profile_text_color profile_use_background_image  \
0         False    False  ...             333333                         True   
1         False    False  ...             333333                         True   
2         False    False  ...             3C3940                         True   
3         False    False  ...             333333                         True   
4         False    False  ...             333333                         True   
...         ...      ...  ...                ...                          ...   
95649     False    False  ...             333333                         True   
95650     False    False  ...             333333                         True   
95651     False    False  ...             000000                        False   
95652     False    False  ...             333333                         True   
95653     False    False  ...             333333                         True   

                                       profile_image_url  \
0      http://pbs.twimg.com/profile_images/1246253579...   

In [35]:
session.use_database('COVID19_NEW')

In [36]:
session.use_schema('RAW_DATA')

In [37]:
session.write_pandas(user_df,auto_create_table=True,table_name='USER_TABLE')